In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

In [2]:
import itertools
import os
import math
import numpy as np
import pandas as pd
import tensorflow as tf

from sklearn.preprocessing import LabelEncoder
from tensorflow import keras
layers = keras.layers

# This code was tested with TensorFlow v1.7
print("You have TensorFlow version", tf.__version__)

You have TensorFlow version 1.13.1


In [3]:
# Get the data: original source is here: https://www.kaggle.com/zynicide/wine-reviews/data
URL = "https://final-project-99.s3-ap-southeast-1.amazonaws.com/wine.csv"
path = tf.keras.utils.get_file(URL.split('/')[-1], URL)


In [4]:
# Convert the data to a Pandas data frame
data = pd.read_csv(path)

In [5]:
# Shuffle the data
data = data.sample(frac=1)

# Print the first 5 rows
data.head()

Unnamed: 0 country                                        description  \
73839        73839  France  Full in the mouth, this is a tight, caramel an...   
137331      137331   Italy  In contrast to Tommasi's regular Amarone, this...   
57700        57700   Italy  Here's a Sicilian dessert wine that stands out...   
64604        64604      US  This is half estate-grown Sangiovese but done ...   
7330          7330  France  With great acidity, this wine that comes from ...   

          designation  points  price           province  \
73839   Clos Mireille      90   46.0           Provence   
137331    Ca' Florian      92   68.0             Veneto   
57700       Il Musico      87   26.0  Sicily & Sardinia   
64604      Juliet Red      91   40.0         Washington   
7330              NaN      92   60.0           Bordeaux   

                                   region_1         region_2  \
73839                     Côtes de Provence              NaN   
137331  Amarone della Valpolicella Classico              NaN   
57700                               Sicilia              NaN   
64604               Walla Walla Valley (WA)  Columbia Valley   
7330                          Saint-Émilion              NaN   

                              variety               winery  
73839                            Rosé         Domaines Ott  
137331  Corvina, Rondinella, Molinara              Tommasi  
57700                         Moscato              Benanti  
64604                       Red Blend        Nicholas Cole  
7330         Bordeaux-style Red Blend  Clos Badon-Thunevin

In [6]:
# Do some preprocessing to limit the # of wine varities in the dataset
data = data[pd.notnull(data['country'])]
data = data[pd.notnull(data['price'])]
data = data.drop(data.columns[0], axis=1) 

variety_threshold = 250 # Anything that occurs less than this will be removed.
value_counts = data['variety'].value_counts()
to_remove = value_counts[value_counts <= variety_threshold].index
data.replace(to_remove, np.nan, inplace=True)
data = data[pd.notnull(data['variety'])]

In [7]:
# Split data into train and test
train_size = int(len(data) * .75)
print ("Train size: %d" % train_size)
print ("Test size: %d" % (len(data) - train_size))

Train size: 93588
Test size: 31196


In [8]:
# Train features
description_train = data['description'][:train_size]
variety_train = data['variety'][:train_size]

# Train labels
labels_train = data['price'][:train_size]

# Test features
description_test = data['description'][train_size:]
variety_test = data['variety'][train_size:]

# Test labels
labels_test = data['price'][train_size:]

In [9]:
# Create a tokenizer to preprocess our text descriptions
vocab_size = 20000 # This is a hyperparameter, experiment with different values for your dataset
tokenize = keras.preprocessing.text.Tokenizer(num_words=vocab_size, char_level=False)
tokenize.fit_on_texts(description_train) # only fit on train

In [10]:
# Wide feature 1: sparse bag of words (bow) vocab_size vector 
description_bow_train = tokenize.texts_to_matrix(description_train)
description_bow_test = tokenize.texts_to_matrix(description_test)

In [11]:
# Wide feature 2: one-hot vector of variety categories

# Use sklearn utility to convert label strings to numbered index
encoder = LabelEncoder()
encoder.fit(variety_train)
variety_train = encoder.transform(variety_train)
variety_test = encoder.transform(variety_test)
num_classes = np.max(variety_train) + 1

# Convert labels to one hot
variety_train = keras.utils.to_categorical(variety_train, num_classes)
variety_test = keras.utils.to_categorical(variety_test, num_classes)

In [12]:
# Define our wide model with the functional API
bow_inputs = layers.Input(shape=(vocab_size,))
variety_inputs = layers.Input(shape=(num_classes,))
merged_layer = layers.concatenate([bow_inputs, variety_inputs])
merged_layer = layers.Dense(256, activation='relu')(merged_layer)
predictions = layers.Dense(1)(merged_layer)
wide_model = keras.Model(inputs=[bow_inputs, variety_inputs], outputs=predictions)

Instructions for updating:
Colocations handled automatically by placer.


In [13]:
wide_model.compile(loss='mse', optimizer='adam', metrics=['mae', 'mape'])
print(wide_model.summary())

Instructions for updating:
Use tf.cast instead.
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 20000)        0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            (None, 55)           0                                            
__________________________________________________________________________________________________
concatenate (Concatenate)       (None, 20055)        0           input_1[0][0]                    
                                                                 input_2[0][0]                    
__________________________________________________________________________________________________
dense (Dense)                   (None, 256)          5134336 

In [14]:
# Deep model feature: word embeddings of wine descriptions
train_embed = tokenize.texts_to_sequences(description_train)
test_embed = tokenize.texts_to_sequences(description_test)

max_seq_length = 175
train_embed = keras.preprocessing.sequence.pad_sequences(
    train_embed, maxlen=max_seq_length, padding="post")
test_embed = keras.preprocessing.sequence.pad_sequences(
    test_embed, maxlen=max_seq_length, padding="post")

In [15]:
# Define our deep model with the Functional API
deep_inputs = layers.Input(shape=(max_seq_length,))
embedding = layers.Embedding(vocab_size, 8, input_length=max_seq_length)(deep_inputs)
embedding = layers.Flatten()(embedding)
embed_out = layers.Dense(1)(embedding)
deep_model = keras.Model(inputs=deep_inputs, outputs=embed_out)
print(deep_model.summary())

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         (None, 175)               0         
_________________________________________________________________
embedding (Embedding)        (None, 175, 8)            160000    
_________________________________________________________________
flatten (Flatten)            (None, 1400)              0         
_________________________________________________________________
dense_2 (Dense)              (None, 1)                 1401      
Total params: 161,401
Trainable params: 161,401
Non-trainable params: 0
_________________________________________________________________
None


In [16]:
deep_model.compile(loss='mse', optimizer='adam', metrics=['mae', 'mape'])

In [17]:
# Combine wide and deep into one model
merged_out = layers.concatenate([wide_model.output, deep_model.output])
merged_out = layers.Dense(1)(merged_out)
combined_model = keras.Model(wide_model.input + [deep_model.input], merged_out)
print(combined_model.summary())

combined_model.compile(loss='mse', optimizer='adam', metrics=['mae', 'mape'])

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 20000)        0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            (None, 55)           0                                            
__________________________________________________________________________________________________
input_3 (InputLayer)            (None, 175)          0                                            
__________________________________________________________________________________________________
concatenate (Concatenate)       (None, 20055)        0           input_1[0][0]                    
                                                                 input_2[0][0]                    
__________

In [18]:
# Run training
combined_model.fit([description_bow_train, variety_train] + [train_embed], labels_train, epochs=250, batch_size=128)

Instructions for updating:
Use tf.cast instead.
Epoch 1/250
93588/93588 [==============================] - 89s 949us/sample - loss: 1092.4903 - mean_absolute_error: 15.3174 - mean_absolute_percentage_error: 53.4649
Epoch 2/250
93588/93588 [==============================] - 89s 950us/sample - loss: 840.1770 - mean_absolute_error: 12.8159 - mean_absolute_percentage_error: 42.7409
Epoch 3/250
93588/93588 [==============================] - 92s 987us/sample - loss: 693.5025 - mean_absolute_error: 11.6953 - mean_absolute_percentage_error: 38.9615
Epoch 4/250
93588/93588 [==============================] - 91s 967us/sample - loss: 563.7060 - mean_absolute_error: 10.6234 - mean_absolute_percentage_error: 35.8013
Epoch 5/250
93588/93588 [==============================] - 84s 900us/sample - loss: 454.0728 - mean_absolute_error: 9.5348 - mean_absolute_percentage_error: 32.7102
Epoch 6/250
93588/93588 [==============================] - 84s 902us/sample - loss: 364.1357 - mean_absolute_error: 8.5851

93588/93588 [==============================] - 84s 898us/sample - loss: 10.1039 - mean_absolute_error: 1.6255 - mean_absolute_percentage_error: 5.9540
Epoch 49/250
93588/93588 [==============================] - 89s 946us/sample - loss: 9.7995 - mean_absolute_error: 1.6136 - mean_absolute_percentage_error: 5.8972
Epoch 50/250
93588/93588 [==============================] - 89s 951us/sample - loss: 9.7571 - mean_absolute_error: 1.5860 - mean_absolute_percentage_error: 5.8378- loss: 9.7221 - mean_absolute_error: 1.5856 - mean_absolute_percentage_error: 
Epoch 51/250
93588/93588 [==============================] - 90s 963us/sample - loss: 9.6768 - mean_absolute_error: 1.5977 - mean_absolute_percentage_error: 5.8713
Epoch 52/250
93588/93588 [==============================] - 89s 956us/sample - loss: 8.5577 - mean_absolute_error: 1.5314 - mean_absolute_percentage_error: 5.6244
Epoch 53/250
93588/93588 [==============================] - 87s 928us/sample - loss: 8.7939 - mean_absolute_error: 1.5

93588/93588 [==============================] - 84s 892us/sample - loss: 5.5606 - mean_absolute_error: 1.2123 - mean_absolute_percentage_error: 4.4831
Epoch 98/250
93588/93588 [==============================] - 85s 912us/sample - loss: 5.0279 - mean_absolute_error: 1.1685 - mean_absolute_percentage_error: 4.3379
Epoch 99/250
93588/93588 [==============================] - 85s 912us/sample - loss: 4.9872 - mean_absolute_error: 1.1526 - mean_absolute_percentage_error: 4.2744
Epoch 100/250
93588/93588 [==============================] - 84s 899us/sample - loss: 4.6548 - mean_absolute_error: 1.1226 - mean_absolute_percentage_error: 4.1752
Epoch 101/250
93588/93588 [==============================] - 83s 885us/sample - loss: 4.7658 - mean_absolute_error: 1.1373 - mean_absolute_percentage_error: 4.2447
Epoch 102/250
93588/93588 [==============================] - 86s 918us/sample - loss: 4.6372 - mean_absolute_error: 1.1470 - mean_absolute_percentage_error: 4.2668
Epoch 103/250
93588/93588 [=====

93588/93588 [==============================] - 90s 965us/sample - loss: 3.4373 - mean_absolute_error: 0.9579 - mean_absolute_percentage_error: 3.5701
Epoch 148/250
93588/93588 [==============================] - 83s 890us/sample - loss: 3.1506 - mean_absolute_error: 0.9328 - mean_absolute_percentage_error: 3.4833
Epoch 149/250
93588/93588 [==============================] - 84s 901us/sample - loss: 3.3524 - mean_absolute_error: 0.9580 - mean_absolute_percentage_error: 3.5602
Epoch 150/250
93588/93588 [==============================] - 83s 885us/sample - loss: 3.2904 - mean_absolute_error: 0.9642 - mean_absolute_percentage_error: 3.6042
Epoch 151/250
93588/93588 [==============================] - 85s 905us/sample - loss: 3.3424 - mean_absolute_error: 0.9677 - mean_absolute_percentage_error: 3.6160
Epoch 152/250
93588/93588 [==============================] - 84s 902us/sample - loss: 3.4466 - mean_absolute_error: 0.9594 - mean_absolute_percentage_error: 3.5612
Epoch 153/250
93588/93588 [===

93588/93588 [==============================] - 86s 922us/sample - loss: 2.4271 - mean_absolute_error: 0.8289 - mean_absolute_percentage_error: 3.0991
Epoch 198/250
93588/93588 [==============================] - 86s 923us/sample - loss: 2.4709 - mean_absolute_error: 0.8363 - mean_absolute_percentage_error: 3.1279
Epoch 199/250
93588/93588 [==============================] - 86s 922us/sample - loss: 2.5005 - mean_absolute_error: 0.8415 - mean_absolute_percentage_error: 3.1547
Epoch 200/250
93588/93588 [==============================] - 84s 892us/sample - loss: 2.4410 - mean_absolute_error: 0.8394 - mean_absolute_percentage_error: 3.1565
Epoch 201/250
93588/93588 [==============================] - 83s 883us/sample - loss: 2.5137 - mean_absolute_error: 0.8442 - mean_absolute_percentage_error: 3.1603
Epoch 202/250
93588/93588 [==============================] - 85s 911us/sample - loss: 2.4496 - mean_absolute_error: 0.8302 - mean_absolute_percentage_error: 3.1090
Epoch 203/250
93588/93588 [===

93588/93588 [==============================] - 92s 986us/sample - loss: 1.7988 - mean_absolute_error: 0.7326 - mean_absolute_percentage_error: 2.7499
Epoch 247/250
93588/93588 [==============================] - 89s 952us/sample - loss: 1.9700 - mean_absolute_error: 0.7557 - mean_absolute_percentage_error: 2.8357
Epoch 248/250
93588/93588 [==============================] - 84s 898us/sample - loss: 2.1595 - mean_absolute_error: 0.7831 - mean_absolute_percentage_error: 2.9591
Epoch 249/250
93588/93588 [==============================] - 86s 914us/sample - loss: 2.0460 - mean_absolute_error: 0.7544 - mean_absolute_percentage_error: 2.8376
Epoch 250/250
93588/93588 [==============================] - 88s 945us/sample - loss: 1.7977 - mean_absolute_error: 0.7274 - mean_absolute_percentage_error: 2.7307


In [19]:
combined_model.evaluate([description_bow_test, variety_test] + [test_embed], labels_test, verbose=1, batch_size=128)

31196/31196 [==============================] - 35s 1ms/sample - loss: 707.3979 - mean_absolute_error: 9.2053 - mean_absolute_percentage_error: 31.5439


[707.3979176250937, 9.205322, 31.543869]

In [20]:
# Generate predictions
predictions = combined_model.predict([description_bow_test, variety_test] + [test_embed])

In [21]:
# Compare predictions with actual values for the first few items in our test dataset
num_predictions = 20000
diff = 0

for i in range(num_predictions):
    val = predictions[i]
    print(description_test.iloc[i])
    print('Predicted: ', val[0])
    print('Actual: ', labels_test.iloc[i], '\n')
    diff += abs(val[0] - labels_test.iloc[i])

Tart berries, a touch of maple syrup and some orange peel on the nose open into a dry black-cherry palate and lean mouthfeel. Sharply austere.
Predicted:  14.139949
Actual:  43.0 

Very dense tannins dominate big ripe blackberry jam flavors. The wine is hugely rich, but sustains itself by the structure which is dry, dusty tannin-dominated, with just a hint of fruit. To finish, there are juicy, fresh flavors.
Predicted:  11.55923
Actual:  12.0 

This cooperative winery offers good quality at bargain prices. Here's a rich Amarone with lively chocolate, black cherry, vanilla and spice components. The sweet, penetrating bouquet is further enhanced by light shadings of steak sauce and cola.
Predicted:  29.999708
Actual:  30.0 

Clove and other challenging aromas greet you, and never does this blend of Malbec, Cabernet, Bonarda and Merlot get it fully together. The palate seems a little reduced and short on feel, and while it widens and softens on the finish, the ride to get there is bumpy. 

Probably not to everyone's liking, but this oak-fermented Verdejo is a bit like Burgundy and/or white Bordeaux. Cured meat, match stick and pineapple-lemon aromas work their way onto the mildly oaky nose, while the palate has a vanilla-based lushness that works well. Rich, opulent and classy. A sincere food wine.
Predicted:  35.427197
Actual:  35.0 

The challenge for the winemaker in future vintages is to tame these hard, fierce tannins. With sour cherry candy and sandalwood flavors and tart acidity, this '11 is rustic-chic. Enjoy with an upscale hamburger.
Predicted:  23.41997
Actual:  25.0 

Dark for a rosé, and heavy in texture, with berry and cocoa flavors. Lacks charm, but at least it's dry.
Predicted:  12.279825
Actual:  12.0 

Baked red apple, soft peach and a touch of whole vanilla bean fill the bouquet, while notes of clementine rind and soft wood develop in the mouth. Round but not fat with medium acid and a solid finish. Drink now.
Predicted:  14.860712
Actual:  15.0 

Eart

Actual:  21.0 

Mostly made of Cabernet and Syrah, this has strong coffee-liqueur and vanilla syrup flavors, along with a concentrated raspberry note. It has a slightly sweet impression, and there is plenty of power to the flavors.
Predicted:  35.735813
Actual:  35.0 

A darker, quite savory expression of Black Kite's entire vineyard site in the Deep End of Anderson Valley, this Pinot imparts a touch of cardamom spice and high acidity, with a dryness to the finish that gets a lift from that acid at the end.
Predicted:  44.34545
Actual:  45.0 

A light mauve in color, this Pinot Noir-based wine shows boisterous plum fruit, macerated strawberries and a hint of clove on the ripe nose, making it more entrée-ready than apéritif-aimed. The palate offers strawberry and bubble-gum notes deftly hidden behind a veil of sour cherry and plum-skin tartness.
Predicted:  17.035679
Actual:  18.0 

Still young, this is a wine that needs to open and ripen. But already there are signs of richness, a wood

Actual:  20.0 

Starts with a hint of honey to go with Asian pear and dried spices, developing into a medium-bodied, round Riesling with strong apple, pear, spice and tangerine flavors. It could be a touch longer on the finish, but it does have a pleasant tactile quality that gives it added refreshment.
Predicted:  19.12204
Actual:  19.0 

Too sharply acidic and jammy in cherries and raspberries, with a hard scour of tannins. It's tasty, but unsophisticated, even for Petite Sirah. Could surprise with lots of time in the cellar, but will never outgrow its rustic personality.
Predicted:  24.88476
Actual:  24.0 

A stunning Pirouette—63% Cabernet Sauvignon, 22% Merlot, 9% Cab Franc and 6% Petit Verdot. Full and magnificently rich, it is loaded with dense and thrilling fruit flavors of black cherry and cassis. A streak of iron and a hint of citrus keep the wine evolving through a long, beautifully balanced finish. Retasted after being open for 24 hours, the wine was as fresh and thrilling 

Give this Burgundian-style Chardonnay some extra breathing time and it rewards you with tight, fine-spun and complex flavors of lemon meringue, orange peel and brioche, with a streak of creamy vanilla. It's the sort of wine that invites reflection and rewards patience.
Predicted:  17.937733
Actual:  45.0 

This would be a wonderful wine even if it cost a little more. As it is, it's a steal. Shows refined apricot, peach, lychee, mineral and floral flavors, finished with brisk, mouthwatering acidity, and an absolutely dry finish. One of the best Riesling values available in Cailfornia, and a tremendous cocktail wine. Just 600 cases were produced.
Predicted:  14.695144
Actual:  15.0 

Too soft for comfort. Lacks structural integrity and lively acidity to balance out the rich blackberry, currant, anise and cocoa flavors, and there's peppery heat from high alcohol. Drink now.
Predicted:  44.159073
Actual:  44.0 

This is herbal, with some flavors of green bell pepper and wild spice. The win

...

Predicted:  23.79997
Actual:  37.0 

Earthy but sharp on the nose, with a foreboding sense of stem and sourness. The palate is indeed raw and acidic, with lean, slightly stemmy flavors of herbs, raspberry and plum. Not bad but carries a stemmy, less-than-pure personality.
Predicted:  14.359414
Actual:  14.0 

This light and pleasant rosé comes exclusively from estate-grown fruit. Cool fermented in stainless steel, it shows delicate strawberry flavors, and a finishing wash of mineral.
Predicted:  18.935091
Actual:  17.0 

A classically fruity Beaujolais from the south of the region, this is packed with bitter cherry and ripe raspberry flavors. The tannins are soft—plentiful enough to lend structure. It is delicious, juicy and ready to drink.
Predicted:  15.245721
Actual:  15.0 

Light in body and frankly a little skinny, this is nevertheless a pretty wine, its tannic structure of skillfully woven silk. Subtle cherry and sous bois notes aren't overly powerful, but persist nicely on the f

Predicted:  35.671772
Actual:  36.0 

The aromas here are seriously woody, and that problem also appears on the palate. It has fruit, but the weight to balance is not there yet. This should develop over the next 4–5 years, but the wood is always going to be a major feature.
Predicted:  25.354916
Actual:  25.0 

This is soft, fruity and very approachable, with flavors of strawberry jam. Highlights of sassafras and a pleasing spiciness add texture and interest.
Predicted:  39.376083
Actual:  40.0 

This is a lightly creamy, fruity wine. With touches of citrus, bitter orange and a good burst of acidity, it is balanced, ripe and ready to drink.
Predicted:  13.090959
Actual:  35.0 

A bright, immediate delivery of fresh tones of cut grass, white flowers and citrus emerge from the nose of this cheerful Soave Classico. The wine promises food-friendliness on all levels thanks to the simplicity of its style and its crisp acidity.
Predicted:  12.739894
Actual:  13.0 

Simple and hot, with uneven

This is somewhat lean, but its elegantly tailored in its brisk acidity and dryness. While the cherry and berry flavors are modest, the wine's austerity makes it versatile with an enormous range of foods.
Predicted:  12.1471195
Actual:  38.0 

Despite firm tannins and tough acidity this wine is so rich and silky, you can drink it now, with decanting. It floods the mouth with raspberries, cherries, chocolate, anise, cinnamon spice and sweet oak. Absolutely delicious, with a silky, seductive mouthfeel. Although it's the least expensive of Williams Selyem's new releases, it's right up there.
Predicted:  54.214455
Actual:  54.0 

Remarkably good for such a large production Pinot Noir (45,000 cases; 3,510 imported), this wine offers bright cherry fruit augmented by hints of baking spices, brown sugar and toasted almonds. The silky texture is spot-on, and it even finishes well, leaving behind nuanced bits of fruit. Drink now.
Predicted:  19.831972
Actual:  20.0 

A beautiful Chardonnay at a g

Almost amber in color, with both fresh orange and drier orange peel on the nose. This is a solid effort with flavors of honey, apple cider and caramel. It could use another shot of acidity to give it a more balanced mouthfeel, but still it's a nice and pleasant wine.
Predicted:  14.756929
Actual:  15.0 

Stunning. Explodes with the most intricately detailed aromas: a perfume of fine smoky oak and ripe black currants. Exudes sheer power, with great weight yet no heaviness. Lush and delicious, but just tannic enough. If you can wait, cellar until 2008, it should hold and improve for many years.
Predicted:  190.82614
Actual:  185.0 

Pleasant, light, and crisp, it shows pretty aromas of lemons, vanilla and white peaches. It's pretty dry, although there's some ripe sweet fruit in the middle palate.
Predicted:  9.238164
Actual:  10.0 

Sometimes all you need in a wine is for it to be dry, fruity and fun to drink. With a lamb or turkey burger, well-prepared, this is a good companion, jammy a


The winery claims the vines date back to 1882; the wine is a stunner, with rich, old vine complexity mixing cherries, leafy old-vine flavors, smooth chocolaty oak. Smooth, seductive, delicious.
Predicted:  27.054707
Actual:  24.0 

A beautiful Viognier that showcases the variety's rich, exotic side. Offers a mouthburst of ripe grilled peaches, pineapples, green apples, honeysuckle and vanilla wrapped into a creamy, buttery texture. Try as an offbeat alternative to Chardonnay.
Predicted:  27.130816
Actual:  27.0 

Despite containing 50% Viognier, this is a restrained Côtes du Rhône white, with subtle citrus and wet stone shadings and a refined, medium-weight mouthfeel. It finishes well, with plenty of length and hints of citrus and honey. Drink it over the next year or two.
Predicted:  9.783099
Actual:  19.0 

Pretty good for an inexpensive Pinot Noir. It's lacking the richness you really want, but is nice and dry and silky, with pleasant enough cherry and cola flavors and a bright bur

In [22]:
# Compare the average difference between actual price and the model's predicted price
print('Average prediction difference: ', diff / num_predictions)

Average prediction difference:  9.373568000355363


In [23]:
combined_model.save("wine_pricing_model_final.h5")